<div style="text-align: center; background-color: #0A6EBD; font-family: 'Trebuchet MS', Arial, sans-serif; color: white; padding: 20px; font-size: 40px; font-weight: bold; border-radius: 0 0 0 0; box-shadow: 0px 6px 8px rgba(0, 0, 0, 0.2);">
  Final project - Introduction to DS
</div>

<div style="text-align: center; background-color: #b1d1ff; font-family: 'Trebuchet MS', Arial, sans-serif; color: white; padding: 20px; font-size: 40px; font-weight: bold; border-radius: 0 0 0 0; box-shadow: 0px 6px 8px rgba(0, 0, 0, 0.2);">
  Stage 4.0 - Data modelling
</div>

## TODO: Problem statement

## Import

In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split

## Data preparation

Read clean data

In [2]:
clean_df = pd.read_csv('../data/processed/video_data_processed.csv')

In [3]:
clean_df.sample(5)

video_id    channelTitle  \
4886   j25Ltlv1yr4      Tina Huang   
749    vF9QRJwJXJk      Krish Naik   
29182  z74IWFDBf0c      Databricks   
15743  qyzfOuozTEk  Great Learning   
41670  nvF9tQZb3gQ       itversity   

                                                   title  \
4886             Why You Won't Reach Your Full Potential   
749    Video Streaming Using Webcam In Flask Web Fram...   
29182  ADMM Based Scalable Machine Learning on Apache...   
15743  Understanding the IT Layoff and Skill Gaps in ...   
41670  Mastering Python - Performing Database Operati...   

                                             description  \
4886   ✉️ NEWSLETTER: https://tinahuang.substack.com/...   
749    github: https://github.com/krishnaik06/Flask-W...   
29182  Apache Spark is rapidly becoming the de facto ...   
15743  The recent layoffs in the IT industry can pose...   
41670  As part of this module we will perform basic d...   

                                                    tags  \
4886                                             (notag)   
749                                              (notag)   
29182                          apache spark|spark summit   
15743  it layoff|it jobs|analytics education|informat...   
41670  Perform Database Operations|Overview of SQL|Cr...   

                     publishedAt  viewCount  likeCount  commentCount  \
4886   2023-08-16 20:14:18+00:00      42164       2942           194   
749    2021-06-14 15:29:54+00:00      61323       1283            97   
29182  2017-06-12 19:24:16+00:00        543          4             0   
15743  2017-10-06 14:00:05+00:00        276          2             0   
41670  2020-12-22 11:30:27+00:00       1324          5             0   

       duration definition  caption  publishedAt.hour  publishedAt.day  \
4886        577         hd    False                20               16   
749         942         hd    False                15               14   
29182      1415         hd    False                19               12   
15743       174         hd    False                14                6   
41670        99         hd    False                11               22   

       publishedAt.year  publishedAt.month  publishedAt.dayOfWeek  \
4886               2023                  8                      2   
749                2021                  6                      0   
29182              2017                  6                      0   
15743              2017                 10                      4   
41670              2020                 12                      1   

       publishedAt.weekOfYear  
4886                       33  
749                        24  
29182                      24  
15743                      40  
41670                      52

In [4]:
clean_df.columns

Index(['video_id', 'channelTitle', 'title', 'description', 'tags',
       'publishedAt', 'viewCount', 'likeCount', 'commentCount', 'duration',
       'definition', 'caption', 'publishedAt.hour', 'publishedAt.day',
       'publishedAt.year', 'publishedAt.month', 'publishedAt.dayOfWeek',
       'publishedAt.weekOfYear'],
      dtype='object')

In [5]:
# NLP libraries
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
nltk.download('stopwords')
nltk.download('punkt')
from wordcloud import WordCloud
from nltk.tokenize import RegexpTokenizer
import re

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ASUS\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ASUS\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [6]:
clean_df['title']

0                              My top 50 scikit-learn tips
1                                    21 more pandas tricks
2        Adapt this pattern to solve many Machine Learn...
3        Tune multiple models simultaneously with GridS...
4                  Access part of a Pipeline using slicing
                               ...                        
60027                 How to Get Free FME Desktop Licenses
60028               Rest API to S3 with FME | Step by Step
60029                  How To Manage Temporary Data In FME
60030    Creating Points From X,Y Coordinates with FME ...
60031                  FME FeatureJoiner Transformer Guide
Name: title, Length: 60032, dtype: object

In [7]:
stop_words = set(stopwords.words('english'))
# Preprocess the data: convert to lowercase, remove special characters, and stopwords
def preprocess_text(text):
    text = text.lower()
    text = re.sub(r'[^a-z\s]', '', text)
    stop_words = set(stopwords.words('english'))
    tokens = [token for token in text.split() if token not in stop_words]
    return ' '.join(tokens)

# # Remove stop words
# clean_df['title_no_stopwords'] \
#     = clean_df['title'].apply(lambda x: [item for item in str(x).split() 
#                                          if item not in stop_words])
# # Join the words back into one string separated by space
# clean_df['title_no_stopwords'] \
#     = clean_df['title_no_stopwords'].apply(lambda x: ' '.join(x))
# # Lower case
# clean_df['title_no_stopwords'] \
#     = clean_df['title_no_stopwords'].apply(lambda x: x.lower())
clean_df['clean_title'] = clean_df['title'].apply(preprocess_text)

In [8]:
clean_df['clean_title']

0                                     top scikitlearn tips
1                                            pandas tricks
2        adapt pattern solve many machine learning prob...
3         tune multiple models simultaneously gridsearchcv
4                       access part pipeline using slicing
                               ...                        
60027                        get free fme desktop licenses
60028                               rest api fme step step
60029                            manage temporary data fme
60030         creating points xy coordinates fme step step
60031                  fme featurejoiner transformer guide
Name: clean_title, Length: 60032, dtype: object

## Clustering title

In [11]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
import numpy as np

def my_clustering(s): 
    # Your list of text values
    text_values = [
        # ... (paste your list here)
    ]
    text_values = s
    # Convert text to numerical data using TF-IDF
    vectorizer = TfidfVectorizer(stop_words='english')
    X = vectorizer.fit_transform(text_values)

    # Choose the number of clusters (you may need to adjust this based on your data)
    num_clusters = 25

    # Apply K-Means clustering
    kmeans = KMeans(n_clusters=num_clusters, random_state=42)
    kmeans.fit(X)

    # Get cluster labels
    cluster_labels = kmeans.labels_
    # Print the clusters
    for i in range(num_clusters):
        print(f"Cluster {i + 1}:")
        cluster_texts = np.array(text_values)[cluster_labels == i]
        for text in cluster_texts:
            print(f"  - {text}")
        print("\n")

In [12]:
my_clustering(clean_df['clean_title'])

Cluster 1:
  - tutorial pandasreading jsonreading html read pickle read excel files part
  - data analysts hate using excel
  - excel dataanalyst dataanalysis
  - full project excel excel tutorials beginners
  - cleaning data excel excel tutorials beginners
  - charts excel excel tutorials beginners
  - conditional formatting excel excel tutorials beginners
  - xlookup excel excel tutorials beginners
  - formulas excel excel tutorials beginners
  - pivot tables excel excel tutorials beginners
  - introduction python excel users
  - introduction r programming excel users r programming tutorial
  - business data analysis excel master data analysis excel
  - graphing histograms frequency polygons excel
  - excel alternative use sql perform excel tasks sql data analysis
  - python excel microsoft changed everything
  - top excel courses data analysts
  - nightmares microsoft excel
  - use excel data analyst
  - use excel data analyst
  - vs intel mac excel
  - still need excel
  - business

## Clustering tags

# -------------------- BREAK --------------------

## Feature engineering

In [10]:
target = "viewCount"
X = clean_df.copy()
X.drop(target, axis=1, inplace=True)
y = clean_df[target].copy()

cat_cols = [col for col in X.columns if X[col].dtype == "object"]
from sklearn.preprocessing import LabelEncoder
for col in cat_cols:
    le = LabelEncoder()
    X[col] = le.fit_transform(X[col])
    # X_val[col] = le.transform(X_val[col])
    # X_test[col] = le.transform(X_test[col])

In [11]:
X, X_test, y, y_test = train_test_split(X, y, test_size=0.15, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.15, random_state=42)

In [12]:
X_train.shape, X_val.shape, X_test.shape, y_train.shape, y_val.shape, y_test.shape

((43372, 17), (7655, 17), (9005, 17), (43372,), (7655,), (9005,))

## Baseline Model Comparison

In [ ]:
train

In [13]:
from sklearn.linear_model import Lasso, ElasticNet, Ridge
from sklearn.svm import SVR
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor, ExtraTreesRegressor, AdaBoostRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from sklearn.tree import DecisionTreeRegressor
seed = 2023
models = [
    # Lasso(random_state=seed),
    # ElasticNet(random_state=seed),
    # Ridge(random_state=seed),
    # # SVR(),
    # GradientBoostingRegressor(random_state=seed),
    # RandomForestRegressor(random_state=seed),
    # ExtraTreesRegressor(random_state=seed),
    # AdaBoostRegressor(random_state=seed),
    # XGBRegressor(random_state=seed),
    # LGBMRegressor(random_state=seed)
    DecisionTreeRegressor(random_state=seed)
]

In [14]:
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import cross_val_score

def generate_baseline_result(models, X, y, metrics, cv=5, plot_result=False):
    # define k-fold
    kfold = StratifiedKFold(n_splits=cv, shuffle=True, random_state=seed)
    entries = []
    for model in models:
        model_name = model.__class__.__name__
        scores = cross_val_score(model, X, y, scoring=metrics, cv=kfold)
        for fold_idx, score in enumerate(scores):
            entries.append((model_name, fold_idx, score))

    cv_df = pd.DataFrame(entries, columns=['model_name', 'fold_idx', 'score'])
    return cv_df

# Metric: https://scikit-learn.org/stable/modules/model_evaluation.html
generate_baseline_result(models, X_train, y_train, metrics='neg_mean_absolute_error')

d:\All_In_1\Anaconda\anaconda3\envs\min_ds-env\lib\site-packages\sklearn\model_selection\_split.py:737: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


model_name  fold_idx         score
0  DecisionTreeRegressor         0 -22574.289107
1  DecisionTreeRegressor         1 -20390.721499
2  DecisionTreeRegressor         2 -24403.298017
3  DecisionTreeRegressor         3 -19332.012220
4  DecisionTreeRegressor         4 -21713.164976

In [15]:
import lightgbm as lgb 

lgb_params = {"objective" : "regression", "metric" : ["rmse", "mse", "mae"],
              "num_leaves": 200, "learning_rate" : 0.001, 
              "bagging_fraction" : 0.7, "feature_fraction" : 0.5,
              "force_col_wise": True, "min_child_samples" : 500,
              }

model = lgb.LGBMRegressor(**lgb_params)

for i in range(5):
    print(f"Fold {i+1}")
    lgb_train = lgb.Dataset(X_train, label=y_train)
    lgb_val = lgb.Dataset(X_val, label=y_val)
    model = lgb.train(lgb_params, lgb_train, 1000, valid_sets=[lgb_val],
                    # early_stopping_rounds=150, 
                    # verbose_eval=20
                    )

Fold 1
[LightGBM] [Info] Total Bins 2351
[LightGBM] [Info] Number of data points in the train set: 43372, number of used features: 17
[LightGBM] [Info] Start training from score 48090.435973
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

In [16]:
model.best_score["valid_0"]

OrderedDict([('rmse', 283490.19785376673),
             ('l2', 80366692279.1678),
             ('l1', 39624.577618136165)])

In [16]:
clean_df[target].describe()

count     60032.00000
mean       1120.36274
std        8272.34260
min           0.00000
25%          11.00000
50%          55.00000
75%         332.00000
max      571358.00000
Name: likeCount, dtype: float64

## Training model

In [12]:
# YOUR CODE HERE (OPTION) 

## Evaluation

In [13]:
# YOUR CODE HERE (OPTION) 

## Prediction

In [14]:
# YOUR CODE HERE (OPTION) 

## Results analysis

In [15]:
# YOUR CODE HERE (OPTION) 

## Conclusion

**Your conclusion**